# Import

In [9]:
import os
from functools import reduce
from collections import OrderedDict, defaultdict

import requests
from requests.exceptions import ConnectionError, ReadTimeout
from requests.exceptions import ContentDecodingError, TooManyRedirects
import pandas as pd

from db.mongo import MyMongo

pd.set_option('display.max_colwidth', -1)

# Load DB

In [10]:
with MyMongo() as db:
    quote = db.get_df_from_table('audit_quote', 'a1_all')

<--Mongo Connected.
Mongo Connection Closed.-->


# All Columns

In [11]:
quote.columns

Index(['_id', 'url', '국회의원', '뉴스 식별자', '분석제외 여부', '사건/사고 분류1', '사건/사고 분류2',
       '사건/사고 분류3', '언론사', '인용문', '일자', '정보원', '정보원_추출', '키워드', '통합 분류1',
       '통합 분류2', '통합 분류3', '특성추출'],
      dtype='object')

# Index & Cols

In [12]:
idx_백승주 = quote['국회의원']=='백승주'
idx_임이자 = quote['국회의원']=='임이자'
idx_이채익 = quote['국회의원']=='이채익'
idx_민경욱 = quote['국회의원']=='민경욱'
idx_정세균 = quote['국회의원']=='정세균'

# 이날 특별우수위원으로는 이채익, 백승주, 민경욱, 임이자 의원이 선정됐다.
특별우수위원 = ['민경욱', '이채익', '백승주', '임이자']

top7 = ['박용진', '김병욱', '민경욱', '이채익', '황희', '소병훈', '장제원',]
tosee = top7

cols = ['일자', '언론사', '국회의원', '인용문', 'url']

# head()

In [13]:
quote.loc[::,cols].head()

일자    언론사 국회의원  \
0  20181030  헤럴드경제  이상헌   
1  20181030  헤럴드경제  김병욱   
2  20181030  영남일보   강효상   
3  20181030  MBC    김재경   
4  20181030  세계일보   전혜숙   

                                                                                                                 인용문  \
0  현재 외국인 관광객의 80% 정도는 서울 및 수도권에 몰리는 반면, 타 지방을 방문하는 외국인 관광객은 미미한 수준이라며, 실질적 규제혁신과 제도개선을 통해 지방에 제대로 된 관광인프라가 확충되어야 한다   
1  청년실업 등으로 신용등급이 낮고 형편이 어려운 20대가 은행권에서 대출을 받지 못하고 금리가 높은 대부업체로 내몰린 뒤 상환능력이 떨어져 연체율이 증가하고 있는 것                         
2  지난 6월29일 물산업클러스터 위탁운영기관으로 한국환경공단이 한국수자원공사를 제치고 선정된 배경에는 환경부의 밀어주기 의혹이 있다                                            
3  하나는 비준 동의를 해야 하고 하나는 안 해야 하는 차별성이 있는 것이냐                                                                            
4  가정의학과 의사의 경우 선한 의지로 응급진료를 도운 것뿐인데, 오히려 가해자가 된 셈 이처럼 선한 사마리아인들에게 면책을 주지 않으면 아무도 응급상황에서 환자를 돕지 않을 것                   

                                                                                                                     url  
0  https://www.bigkinds.or.kr/news/detailView.do?docId=02100701.20181030084120001&returnCnt=1&sectionDiv=1000&indexName=  
1  https://www.bigkinds.or.kr/news/detailView.do?docId=02100701.20181030081315001&returnCnt=1&sectionDiv=1000&indexName=  
2  https://www.bigkinds.or.kr/news/detailView.do?docId=01500801.20181030072457002&returnCnt=1&sectionDiv=1000&indexName=  
3  https://www.bigkinds.or.kr/news/detailView.do?docId=08100201.20181030064343002&returnCnt=1&sectionDiv=1000&indexName=  
4  https://www.bigkinds.or.kr/news/detailView.do?docId=01100701.20181030060258001&returnCnt=1&sectionDiv=1000&indexName=

# Groupby

## Groupby '국회의원'

In [14]:
grp_member = quote.groupby(['국회의원']).agg({'인용문': 'count'}).sort_values('인용문', ascending=False); grp_member

인용문
국회의원     
박용진   156
김병욱   101
민경욱   84 
이채익   83 
황희    77 
소병훈   77 
장제원   73 
윤관석   67 
권미혁   65 
손혜원   65 
김영우   61 
박완주   59 
박덕흠   59 
김진태   58 
조배숙   58 
박지원   57 
추경호   57 
김도읍   55 
박재호   55 
권성동   54 
박정    53 
이종배   52 
신용현   52 
심재철   52 
홍익표   51 
권은희   51 
이태규   49 
강병원   49 
김영진   46 
유민봉   46 
백혜련   46 
김성식   45 
박주민   44 
박완수   44 
강창일   44 
금태섭   43 
지상욱   43 
유승민   43 
추혜선   43 
이현재   42 
강효상   42 
김현아   42 
최인호   42 
남인순   42 
김규환   42 
김경진   42 
전현희   41 
조원진   41 
정용기   41 
박선숙   41 
정우택   41 
김수민   41 
김경협   41 
김무성   41 
김병관   41 
하태경   40 
박명재   40 
주승용   39 
우원식   39 
이장우   39 
백재현   39 
정진석   39 
주광덕   38 
박맹우   38 
정유섭   38 
신창현   37 
김동철   37 
이은재   37 
이춘석   37 
변재일   37 
김성수   37 
이재정   37 
윤재옥   36 
이진복   36 
한정애   36 
김종회   35 
백승주   35 
김성태   35 
이후삼   35 
이철희   34 
박병석   34 
송희경   34 
송기헌   34 
윤영일   34 
김한정   34 
엄용수   34 
오제세   34 
윤한홍   34 
채이배   34 
이용주   34 
김종석   33 
조승래   33 
송언석   33 
심상정   32 
안호영   32 
김성원   32 
김상훈   32 
정운천   31 
박범계   31 
김현권   31 
박대출   31 
유성엽   31 
김승희   30 
김중로   30 
서영교   30 
최경환   30 
제윤경   30 
권칠승   30 
강훈식   30 
김선동   30 
이동섭   29 
홍철호   29 
김민기   29 
박성중   29 
최도자   29 
성일종   28 
곽대훈   28 
김상희   28 
이상민   28 
조정식   28 
정동영   28 
이은권   28 
민홍철   28 
전희경   27 
최운열   27 
전해철   26 
조응천   26 
박홍근   26 
김광림   26 
박광온   26 
김영호   25 
박영선   25 
장석춘   24 
윤상직   24 
김종민   24 
송영길   24 
곽상도   24 
김순례   23 
김성환   23 
천정배   23 
유동수   23 
김삼화   23 
홍문표   23 
박찬대   23 
송옥주   23 
김정우   22 
김용태   22 
이상헌   22 
이언주   21 
이완영   21 
정인화   21 
이주영   20 
윤일규   20 
윤후덕   20 
정춘숙   20 
유의동   20 
임이자   20 
이정미   20 
함진규   20 
강길부   20 
김종훈   20 
김진표   20 
기동민   20 
박경미   19 
조경태   19 
윤호중   19 
이헌승   19 
윤준호   19 
정태옥   19 
이해찬   19 
김태흠   19 
위성곤   19 
윤영석   19 
이학재   19 
장병완   18 
서청원   18 
전재수   18 
문진국   18 
송석준   18 
이만희   18 
표창원   18 
이철규   17 
안상수   17 
정갑윤   17 
신경민   17 
김관영   16 
김석기   16 
고용진   16 
유승희   16 
서삼석   16 
이용호   16 
심기준   16 
김병기   15 
김재경   15 
심재권   15 
이훈    15 
이용득   15 
추미애   15 
김태년   14 
나경원   14 
김정훈   14 
이종구   14 
김해영   14 
송갑석   14 
김명연   14 
오영훈   14 
이상돈   14 
임종성   13 
주호영   13 
이양수   12 
황영철   12 
홍영표   12 
이인영   12 
김광수   12 
이명수   12 
김두관   12 
김정재   12 
한선교   11 
원유철   11 
염동열   11 
어기구   11 
이수혁   11 
홍문종   11 
김세연   11 
최교일   10 
박주선   10 
오신환   10 
최연혜   10 
신동근   10 
윤상현   10 
최재성   9  
홍의락   9  
김재원   9  
민병두   9  
이혜훈   9  
윤종필   9  
이학영   9  
김종대   8  
김한표   8  
강석진   8  
설훈    8  
이군현   8  
이규희   8  
정병국   8  
장정숙   8  
박주현   7  
윤소하   7  
김기선   7  
이원욱   7  
이종걸   7  
김성찬   7  
김학용   7  
신상진   6  
경대수   6  
유기준   6  
김영주   6  
정양석   6  
전혜숙   6  
손금주   6  
우상호   6  
서형수   5  
이찬열   5  
이종명   5  
박인숙   5  
노웅래   5  
김철민   5  
황주홍   4  
임재훈   4  
김정호   4  
안민석   3  
안규백   3  
강석호   3  
맹성규   3  
원혜영   3  
정종섭   3  
박순자   3  
홍일표   2  
유재중   2  
이정현   2  
이석현   2  
여상규   2  
진영    1  
조훈현   1  
정세균   1  
정성호   1  
인재근   1

In [15]:
# len(quote.loc[idx_민경욱])
# 이날 특별우수위원으로는 이채익, 백승주, 민경욱, 임이자 의원이 선정됐다.
grp_member.loc[특별우수위원, ::]

인용문
국회의원     
민경욱   84 
이채익   83 
백승주   35 
임이자   20

## Groupby '일자' & '국회의원'

In [16]:
pd.set_option('display.max_row', None)

def get_shortest(series):
    hankyung = quote.loc[quote['언론사']=='한국경제']['인용문'].tolist()
    
    def get_hankyung_or_shortest(x, y):
        result = ''
        if x in hankyung:
            result = x
        elif y in hankyung:
            result = y
        else:
            result = x if len(x) <= len(y) else y
        
        return result
    
    return reduce(get_hankyung_or_shortest, series)
#     return reduce(lambda x, y: x if len(x) >= len(y) else y, series)

# def get_shortest(series):
#     return reduce(lambda x, y: x if len(x) <= len(y) else y, series)


grp_date = quote.groupby(['일자', '국회의원']).agg({'인용문': ['count', get_shortest],}); grp_date
grp_date['날짜'] = grp_date.index.get_level_values(0); grp_date
# grp_date.sort_values(['date', ('인용문', 'count')], ascending=[True, False])

인용문  \
              count   
일자       국회의원         
20181010 강길부   3      
         강병원   3      
         강훈식   6      
         경대수   4      
         고용진   3      
         곽대훈   2      
         권미혁   4      
         권성동   1      
         권은희   2      
         권칠승   1      
         금태섭   3      
         기동민   2      
         김경진   18     
         김관영   3      
         김광수   2      
         김규환   1      
         김도읍   9      
         김두관   1      
         김명연   1      
         김무성   7      
         김병관   6      
         김병기   1      
         김병욱   16     
         김삼화   2      
         김상훈   5      
         김상희   7      
         김석기   2      
         김선동   1      
         김성수   9      
         김성식   1      
         김성찬   1      
         김성태   6      
         김성환   8      
         김세연   1      
         김수민   11     
         김승희   3      
         김영주   1      
         김영진   7      
         김용태   2      
         김재원   1      
         김정우   2      
         김정훈   1      
         김종대   2      
         김종석   1      
         김종회   5      
         김종훈   3      
         김중로   7      
         김진태   17     
         김진표   1      
         김철민   2      
         김태흠   1      
         김한정   5      
         김해영   1      
         김현권   6      
         남인순   3      
         노웅래   1      
         민경욱   29     
         민홍철   2      
         박광온   3      
         박대출   6      
         박덕흠   19     
         박맹우   1      
         박명재   1      
         박범계   1      
         박병석   7      
         박선숙   10     
         박성중   5      
         박영선   2      
         박완수   7      
         박완주   10     
         박재호   3      
         박정    2      
         박주민   3      
         박주선   2      
         박지원   6      
         박홍근   1      
         백승주   4      
         백재현   1      
         백혜련   15     
         변재일   10     
         서청원   4      
         서형수   1      
         성일종   3      
         소병훈   4      
         손금주   1      
         손혜원   16     
         송갑석   2      
         송기헌   7      
         송석준   4      
         송언석   1      
         송영길   4      
         송희경   9      
         신동근   1      
         신상진   3      
         신용현   3      
         심상정   2      
         심재권   4      
         심재철   4      
         안민석   2      
         안상수   2      
         안호영   4      
         엄용수   1      
         여상규   1      
         염동열   1      
         오신환   2      
         오영훈   1      
         오제세   2      
         우원식   6      
         위성곤   2      
         유기준   2      
         유성엽   1      
         유승민   1      
         유재중   1      
         윤관석   11     
         윤상직   5      
         윤상현   3      
         윤소하   1      
         윤영일   5      
         윤일규   2      
         윤재옥   3      
         윤한홍   1      
         이규희   1      
         이동섭   2      
         이명수   1      
         이상민   8      
         이상헌   3      
         이수혁   6      
         이양수   4      
         이언주   3      
         이완영   1      
         이용주   6      
         이용호   3      
         이원욱   5      
         이은권   2      
         이은재   4      
         이인영   3      
         이재정   4      
         이종명   2      
         이종배   2      
         이주영   1      
         이진복   2      
         이채익   4      
         이철규   1      
         이철희   4      
         이춘석   5      
         이태규   7      
         이학재   5      
         이해찬   7      
         이헌승   2      
         이현재   7      
         이혜훈   2      
         이후삼   4      
         이훈    2      
         임종성   2      
         장석춘   3      
         장제원   3      
         전해철   1      
         정동영   1      
         정양석   2      
         정용기   4      
         정우택   3      
         정운천   3      
         정유섭   8      
         정인화   1      
         정진석   17     
         정춘숙   3      
         정태옥   1      
         제윤경   9      
         조경태   2      
         조배숙   13     
         조원진   3      
         조응천  

In [17]:
hankyung = quote.loc[quote['언론사']=='한국경제']['인용문'].tolist(); hankyung
# quote.loc[quote['인용문']=='정부가 고용지표 개선을 위해 25개 출연연구기관에 할당 방식으로 두 달짜리 단기 아르바이트를 채용토록 하기에 이르렀다 정부의 비정상적인 국정 운영을 보면 어처구니가 없다'
#          , ['언론사']]=='한국경제'

['수사를 받은 판사들에게 재판을 맡기지 않겠다는 것이 국민의 뜻',
 '공사 직원들이 최장 5년간 휴직을 한 후 매년 260~280명씩 해외연수를 가고 있다 무임수송, 낮은 요금 등을 탓하기 전에 방만한 경영을 고쳐 재정건전성부터 확보해야 한다',
 '(평양 남북 정상회담 당시) 옥류관 행사에서 대기업 총수들이 냉면을 먹는 자리에서 이 위원장이 불쑥 나타나 정색하고 ‘아니, 냉면이 목구멍으로 넘어갑니까’라고 했다',
 '부동산 전자계약 제도가 중개업자 반발로 전국적으로 도입하는 것은 쉽지 않아 보인다 이런 상황이 계속된다면 투기과열지구 등에서 일정 기간 전자계약 시스템을 의무화할 필요가 있다',
 '올해 단기일자리 확대 계획이 없다 단기 인력이 필요 없다는 공문을 보냈던 공단이 하루 만에 비공식적인 통로인 이메일을 통해 계획을 제출했다 공단이 눈치 없이 단기일자리가 필요 없다고 곧이곧대로 보고했다가 기재부의 질타를 받았을 것 갑자기 하루 만에 일손이 1136명이나 필요해질 정도로 급박한 상황이 발생하지는 않았을 것',
 '정치인 출신인 김 장관이 내일 국무회의에서 단기일자리 대책에 대한 문제 제기라도 해보라',
 '대북 반출 제한 품목이 많아서 그러느냐 연락사무소와 관련해선 제재 대상이 아니라는 입장이며 시설 성격상 남쪽에서 공사했더라도 같은 식으로 대처했을 것',
 '일반적으로 건물을 신축하는 데 평당 250만원에서 300만원 정도 드는데 개보수에 이렇게 큰 비용이 들어가는지 납득할 수 없다',
 '철도 연결사업이 지연되는 이유가 무엇이냐',
 '새만금 개발이 졸속, 깜짝쇼가 돼서는 안 된다',
 '국세수입 월별 진도율을 감안하면 올해 국세수입은 300조원 안팎이 될 것 작년 8월 진도율(71.4%)을 감안한 올해 국세수입은 298조6000억원이 된다 최근 3년간(2015~2017년) 8월 평균 진도율 70.7%를 감안했을 땐 301조6000억원에 이를 것 민생경제는 하루하루가 어려운데 정부만 나홀로 호황을 맞고 있는 셈 세수가 전망을 훨씬 초과한다면 정부

In [18]:
grp_date

인용문  \
              count   
일자       국회의원         
20181010 강길부   3      
         강병원   3      
         강훈식   6      
         경대수   4      
         고용진   3      
         곽대훈   2      
         권미혁   4      
         권성동   1      
         권은희   2      
         권칠승   1      
         금태섭   3      
         기동민   2      
         김경진   18     
         김관영   3      
         김광수   2      
         김규환   1      
         김도읍   9      
         김두관   1      
         김명연   1      
         김무성   7      
         김병관   6      
         김병기   1      
         김병욱   16     
         김삼화   2      
         김상훈   5      
         김상희   7      
         김석기   2      
         김선동   1      
         김성수   9      
         김성식   1      
         김성찬   1      
         김성태   6      
         김성환   8      
         김세연   1      
         김수민   11     
         김승희   3      
         김영주   1      
         김영진   7      
         김용태   2      
         김재원   1      
         김정우   2      
         김정훈   1      
         김종대   2      
         김종석   1      
         김종회   5      
         김종훈   3      
         김중로   7      
         김진태   17     
         김진표   1      
         김철민   2      
         김태흠   1      
         김한정   5      
         김해영   1      
         김현권   6      
         남인순   3      
         노웅래   1      
         민경욱   29     
         민홍철   2      
         박광온   3      
         박대출   6      
         박덕흠   19     
         박맹우   1      
         박명재   1      
         박범계   1      
         박병석   7      
         박선숙   10     
         박성중   5      
         박영선   2      
         박완수   7      
         박완주   10     
         박재호   3      
         박정    2      
         박주민   3      
         박주선   2      
         박지원   6      
         박홍근   1      
         백승주   4      
         백재현   1      
         백혜련   15     
         변재일   10     
         서청원   4      
         서형수   1      
         성일종   3      
         소병훈   4      
         손금주   1      
         손혜원   16     
         송갑석   2      
         송기헌   7      
         송석준   4      
         송언석   1      
         송영길   4      
         송희경   9      
         신동근   1      
         신상진   3      
         신용현   3      
         심상정   2      
         심재권   4      
         심재철   4      
         안민석   2      
         안상수   2      
         안호영   4      
         엄용수   1      
         여상규   1      
         염동열   1      
         오신환   2      
         오영훈   1      
         오제세   2      
         우원식   6      
         위성곤   2      
         유기준   2      
         유성엽   1      
         유승민   1      
         유재중   1      
         윤관석   11     
         윤상직   5      
         윤상현   3      
         윤소하   1      
         윤영일   5      
         윤일규   2      
         윤재옥   3      
         윤한홍   1      
         이규희   1      
         이동섭   2      
         이명수   1      
         이상민   8      
         이상헌   3      
         이수혁   6      
         이양수   4      
         이언주   3      
         이완영   1      
         이용주   6      
         이용호   3      
         이원욱   5      
         이은권   2      
         이은재   4      
         이인영   3      
         이재정   4      
         이종명   2      
         이종배   2      
         이주영   1      
         이진복   2      
         이채익   4      
         이철규   1      
         이철희   4      
         이춘석   5      
         이태규   7      
         이학재   5      
         이해찬   7      
         이헌승   2      
         이현재   7      
         이혜훈   2      
         이후삼   4      
         이훈    2      
         임종성   2      
         장석춘   3      
         장제원   3      
         전해철   1      
         정동영   1      
         정양석   2      
         정용기   4      
         정우택   3      
         정운천   3      
         정유섭   8      
         정인화   1      
         정진석   17     
         정춘숙   3      
         정태옥   1      
         제윤경   9      
         조경태   2      
         조배숙   13     
         조원진   3      
         조응천  

# Transform

## Select Top 5

In [20]:
top = 5
grp_top5 = grp_date.groupby(level=0).apply(lambda df: df.sort_values(by=('인용문', 'count'), ascending=False)[:top]); grp_top5
grp_top5.index = grp_top5.index.droplevel(0).droplevel(0); grp_top5
grp_top5 = grp_top5.reset_index(); grp_top5
grp_top5.columns = [' '.join(col).strip() for col in grp_top5.columns.values]; grp_top5
grp_top5 = grp_top5.rename(columns={'인용문 count': '인용 횟수', '인용문 get_shortest': '인용문'}); grp_top5
grp_top5 = grp_top5[['날짜', '국회의원', '인용 횟수', '인용문']]; grp_top5

# grp_top5.columns = grp_top5.columns.droplevel(0); grp_top5

날짜 국회의원  인용 횟수  \
0    20181010  민경욱  29      
1    20181010  박덕흠  19      
2    20181010  김경진  18      
3    20181010  정진석  17      
4    20181010  김진태  17      
5    20181011  손혜원  20      
6    20181011  김무성  18      
7    20181011  김진태  15      
8    20181011  권미혁  15      
9    20181011  황희   14      
10   20181012  장제원  20      
11   20181012  조응천  16      
12   20181012  이은재  15      
13   20181012  김도읍  10      
14   20181012  박대출  10      
15   20181013  박용진  8       
16   20181013  정우택  2       
17   20181013  위성곤  2       
18   20181013  송영길  2       
19   20181013  변재일  2       
20   20181014  전해철  6       
21   20181014  소병훈  6       
22   20181014  김병욱  5       
23   20181014  박용진  4       
24   20181014  이상민  4       
25   20181015  박용진  27      
26   20181015  엄용수  11      
27   20181015  지상욱  11      
28   20181015  권미혁  11      
29   20181015  박완주  10      
30   20181016  박용진  23      
31   20181016  강병원  19      
32   20181016  추경호  16      
33   20181016  황희   15      
34   20181016  심상정  14      
35   20181017  박용진  20      
36   20181017  김영진  13      
37   20181017  박선숙  7       
38   20181017  전희경  6       
39   20181017  권성동  6       
40   20181018  유민봉  17      
41   20181018  김영우  15      
42   20181018  김현아  13      
43   20181018  김규환  13      
44   20181018  김도읍  13      
45   20181019  이채익  26      
46   20181019  유성엽  16      
47   20181019  김영우  16      
48   20181019  조정식  13      
49   20181019  장제원  11      
50   20181020  박완수  4       
51   20181020  소병훈  3       
52   20181020  박용진  3       
53   20181020  장제원  2       
54   20181020  신용현  2       
55   20181021  박용진  7       
56   20181021  박완주  5       
57   20181021  서청원  4       
58   20181021  김종훈  3       
59   20181021  정우택  3       
60   20181022  김경협  13      
61   20181022  황희   10      
62   20181022  김영우  10      
63   20181022  전현희  10      
64   20181022  민경욱  10      
65   20181023  주승용  15      
66   20181023  남인순  14      
67   20181023  권은희  13      
68   20181023  강창일  11      
69   20181023  김영우  10      
70   20181024  한정애  10      
71   20181024  소병훈  8       
72   20181024  민경욱  7       
73   20181024  박재호  7       
74   20181024  김영진  6       
75   20181025  김병욱  7       
76   20181025  홍철호  7       
77   20181025  한정애  7       
78   20181025  윤관석  7       
79   20181025  강효상  7       
80   20181026  김병욱  10      
81   20181026  이재정  8       
82   20181026  김종석  8       
83   20181026  김성태  7       
84   20181026  이진복  6       
85   20181027  강효상  3       
86   20181027  박용진  3       
87   20181027  홍문표  3       
88   20181027  김병욱  2       
89   20181027  권칠승  2       
90   20181028  하태경  13      
91   20181028  소병훈  4       
92   20181028  홍문표  3       
93   20181028  강길부  2       
94   20181028  김종회  2       
95   20181029  박용진  17      
96   20181029  정진석  9       
97   20181029  신용현  9       
98   20181029  이채익  8       
99   20181029  박주민  8       
100  20181030  박주민  5       
101  20181030  김재경  4       
102  20181030  권성동  3       
103  20181030  천정배  3       
104  20181030  장제원  3       

                                                                                                                                                                                                                                                             인용문  
0    2013년부터 2017년까지 수도권에서 그린벨트를 해제한 19개 지역 가운데 작년 말 해제된 경기 부천, 서울 강동, 인천 남동구를 제외한 16개 지역에서 주택 매매가격이 평균 5% 상승했다                                                                                                                                                   
1    국민은행의 30년간 서울 아파트 매매가격지수를 보면 민주당이 집권할 때마다 집값이 폭등한다                                                                                                                                                                                                           
2    구글은 세계 각국의 조세법을 어겨가며 수치스러운 장사를 하고 있다                                                                                                                      

## Merge URL

In [21]:
df_top5 = grp_top5.merge(quote.loc[::, ['인용문', '언론사', '뉴스 식별자', 'url']], how='left', on='인용문'); df_top5

날짜 국회의원  인용 횟수  \
0    20181010  민경욱  29      
1    20181010  박덕흠  19      
2    20181010  김경진  18      
3    20181010  정진석  17      
4    20181010  김진태  17      
5    20181011  손혜원  20      
6    20181011  김무성  18      
7    20181011  김진태  15      
8    20181011  권미혁  15      
9    20181011  황희   14      
10   20181012  장제원  20      
11   20181012  조응천  16      
12   20181012  이은재  15      
13   20181012  김도읍  10      
14   20181012  박대출  10      
15   20181013  박용진  8       
16   20181013  박용진  8       
17   20181013  정우택  2       
18   20181013  위성곤  2       
19   20181013  송영길  2       
20   20181013  변재일  2       
21   20181014  전해철  6       
22   20181014  전해철  6       
23   20181014  전해철  6       
24   20181014  전해철  6       
25   20181014  전해철  6       
26   20181014  소병훈  6       
27   20181014  김병욱  5       
28   20181014  박용진  4       
29   20181014  이상민  4       
30   20181015  박용진  27      
31   20181015  엄용수  11      
32   20181015  지상욱  11      
33   20181015  권미혁  11      
34   20181015  박완주  10      
35   20181016  박용진  23      
36   20181016  강병원  19      
37   20181016  추경호  16      
38   20181016  황희   15      
39   20181016  황희   15      
40   20181016  황희   15      
41   20181016  황희   15      
42   20181016  심상정  14      
43   20181017  박용진  20      
44   20181017  김영진  13      
45   20181017  박선숙  7       
46   20181017  박선숙  7       
47   20181017  전희경  6       
48   20181017  권성동  6       
49   20181018  유민봉  17      
50   20181018  김영우  15      
51   20181018  김현아  13      
52   20181018  김규환  13      
53   20181018  김도읍  13      
54   20181019  이채익  26      
55   20181019  이채익  26      
56   20181019  유성엽  16      
57   20181019  유성엽  16      
58   20181019  김영우  16      
59   20181019  조정식  13      
60   20181019  장제원  11      
61   20181020  박완수  4       
62   20181020  소병훈  3       
63   20181020  박용진  3       
64   20181020  박용진  3       
65   20181020  장제원  2       
66   20181020  장제원  2       
67   20181020  신용현  2       
68   20181020  신용현  2       
69   20181021  박용진  7       
70   20181021  박완주  5       
71   20181021  서청원  4       
72   20181021  김종훈  3       
73   20181021  정우택  3       
74   20181022  김경협  13      
75   20181022  황희   10      
76   20181022  김영우  10      
77   20181022  전현희  10      
78   20181022  민경욱  10      
79   20181023  주승용  15      
80   20181023  남인순  14      
81   20181023  권은희  13      
82   20181023  강창일  11      
83   20181023  김영우  10      
84   20181024  한정애  10      
85   20181024  소병훈  8       
86   20181024  민경욱  7       
87   20181024  박재호  7       
88   20181024  김영진  6       
89   20181025  김병욱  7       
90   20181025  홍철호  7       
91   20181025  한정애  7       
92   20181025  한정애  7       
93   20181025  윤관석  7       
94   20181025  강효상  7       
95   20181026  김병욱  10      
96   20181026  김병욱  10      
97   20181026  이재정  8       
98   20181026  김종석  8       
99   20181026  김종석  8       
100  20181026  김종석  8       
101  20181026  김성태  7       
102  20181026  이진복  6       
103  20181027  강효상  3       
104  20181027  박용진  3       
105  20181027  홍문표  3       
106  20181027  김병욱  2       
107  20181027  권칠승  2       
108  20181028  하태경  13      
109  20181028  소병훈  4       
110  20181028  소병훈  4       
111  20181028  홍문표  3       
112  20181028  강길부  2       
113  20181028  김종회  2       
114  20181029  박용진  17      
115  20181029  정진석  9       
116  20181029  신용현  9       
117  20181029  이채익  8       
118  20181029  박주민  8       
119  20181030  박주민  5       
120  20181030  김재경  4       
121  20181030  권성동  3       
122  20181030  천정배  3       
123  20181030  장제원  3       

                                                                                                                                                                                                                                                             인용문  \
0    2013년부터 2017년까지 수도권에서 그린벨트를 해제한 19개 지역 가운데 작년 말 해제된 경기 부천, 서울 강동, 인천 남동구를 제외한 16개 지역에서 주택 매매가격이 평균 5% 상승했다              

In [22]:
df_top5.drop_duplicates(['날짜', '인용문'], inplace=True); df_top5

날짜 국회의원  인용 횟수  \
0    20181010  민경욱  29      
1    20181010  박덕흠  19      
2    20181010  김경진  18      
3    20181010  정진석  17      
4    20181010  김진태  17      
5    20181011  손혜원  20      
6    20181011  김무성  18      
7    20181011  김진태  15      
8    20181011  권미혁  15      
9    20181011  황희   14      
10   20181012  장제원  20      
11   20181012  조응천  16      
12   20181012  이은재  15      
13   20181012  김도읍  10      
14   20181012  박대출  10      
15   20181013  박용진  8       
17   20181013  정우택  2       
18   20181013  위성곤  2       
19   20181013  송영길  2       
20   20181013  변재일  2       
21   20181014  전해철  6       
26   20181014  소병훈  6       
27   20181014  김병욱  5       
28   20181014  박용진  4       
29   20181014  이상민  4       
30   20181015  박용진  27      
31   20181015  엄용수  11      
32   20181015  지상욱  11      
33   20181015  권미혁  11      
34   20181015  박완주  10      
35   20181016  박용진  23      
36   20181016  강병원  19      
37   20181016  추경호  16      
38   20181016  황희   15      
42   20181016  심상정  14      
43   20181017  박용진  20      
44   20181017  김영진  13      
45   20181017  박선숙  7       
47   20181017  전희경  6       
48   20181017  권성동  6       
49   20181018  유민봉  17      
50   20181018  김영우  15      
51   20181018  김현아  13      
52   20181018  김규환  13      
53   20181018  김도읍  13      
54   20181019  이채익  26      
56   20181019  유성엽  16      
58   20181019  김영우  16      
59   20181019  조정식  13      
60   20181019  장제원  11      
61   20181020  박완수  4       
62   20181020  소병훈  3       
63   20181020  박용진  3       
65   20181020  장제원  2       
67   20181020  신용현  2       
69   20181021  박용진  7       
70   20181021  박완주  5       
71   20181021  서청원  4       
72   20181021  김종훈  3       
73   20181021  정우택  3       
74   20181022  김경협  13      
75   20181022  황희   10      
76   20181022  김영우  10      
77   20181022  전현희  10      
78   20181022  민경욱  10      
79   20181023  주승용  15      
80   20181023  남인순  14      
81   20181023  권은희  13      
82   20181023  강창일  11      
83   20181023  김영우  10      
84   20181024  한정애  10      
85   20181024  소병훈  8       
86   20181024  민경욱  7       
87   20181024  박재호  7       
88   20181024  김영진  6       
89   20181025  김병욱  7       
90   20181025  홍철호  7       
91   20181025  한정애  7       
93   20181025  윤관석  7       
94   20181025  강효상  7       
95   20181026  김병욱  10      
97   20181026  이재정  8       
98   20181026  김종석  8       
101  20181026  김성태  7       
102  20181026  이진복  6       
103  20181027  강효상  3       
104  20181027  박용진  3       
105  20181027  홍문표  3       
106  20181027  김병욱  2       
107  20181027  권칠승  2       
108  20181028  하태경  13      
109  20181028  소병훈  4       
111  20181028  홍문표  3       
112  20181028  강길부  2       
113  20181028  김종회  2       
114  20181029  박용진  17      
115  20181029  정진석  9       
116  20181029  신용현  9       
117  20181029  이채익  8       
118  20181029  박주민  8       
119  20181030  박주민  5       
120  20181030  김재경  4       
121  20181030  권성동  3       
122  20181030  천정배  3       
123  20181030  장제원  3       

                                                                                                                                                                                                                                                             인용문  \
0    2013년부터 2017년까지 수도권에서 그린벨트를 해제한 19개 지역 가운데 작년 말 해제된 경기 부천, 서울 강동, 인천 남동구를 제외한 16개 지역에서 주택 매매가격이 평균 5% 상승했다                                                                                                                                                    
1    국민은행의 30년간 서울 아파트 매매가격지수를 보면 민주당이 집권할 때마다 집값이 폭등한다                                                                                                                                                                                                            
2    구글은 세계 각국의 조세법을 어겨가며 수치스러운 장사를 하고 있다                                                                                                                   

In [23]:
len(df_top5)

105

## Fetch hankyung URL

In [24]:

requests_error = []
status_error = []

for i, row in df_top5.iterrows():
#     if i == 2:
#         break

    if row['url']:
        url = row['url']
        
        try:
            response = requests.get(url, timeout=3, verify=False)

        except ReadTimeout:
            requests_error.append(i)
            continue
        except ContentDecodingError:
            requests_error.append(i)
            continue
        except TooManyRedirects:
            requests_error.append(i)
            continue

        if str(response.status_code)[0] == '4':
            status_error.append(i)

        hankyung_url = response.json()['detail']['PROVIDER_LINK_PAGE']
        df_top5.at[i, 'url_hankyung'] = hankyung_url

df_top5

/usr/local/lib/python3.7/site-packages/urllib3/connectionpool.py:857: InsecureRequestWarning: Unverified HTTPS request is being made. Adding certificate verification is strongly advised. See: https://urllib3.readthedocs.io/en/latest/advanced-usage.html#ssl-warnings
  InsecureRequestWarning)
/usr/local/lib/python3.7/site-packages/urllib3/connectionpool.py:857: InsecureRequestWarning: Unverified HTTPS request is being made. Adding certificate verification is strongly advised. See: https://urllib3.readthedocs.io/en/latest/advanced-usage.html#ssl-warnings
  InsecureRequestWarning)
/usr/local/lib/python3.7/site-packages/urllib3/connectionpool.py:857: InsecureRequestWarning: Unverified HTTPS request is being made. Adding certificate verification is strongly advised. See: https://urllib3.readthedocs.io/en/latest/advanced-usage.html#ssl-warnings
  InsecureRequestWarning)
/usr/local/lib/python3.7/site-packages/urllib3/connectionpool.py:857: InsecureRequestWarning: Unverified HTTPS request is be

/usr/local/lib/python3.7/site-packages/urllib3/connectionpool.py:857: InsecureRequestWarning: Unverified HTTPS request is being made. Adding certificate verification is strongly advised. See: https://urllib3.readthedocs.io/en/latest/advanced-usage.html#ssl-warnings
  InsecureRequestWarning)
/usr/local/lib/python3.7/site-packages/urllib3/connectionpool.py:857: InsecureRequestWarning: Unverified HTTPS request is being made. Adding certificate verification is strongly advised. See: https://urllib3.readthedocs.io/en/latest/advanced-usage.html#ssl-warnings
  InsecureRequestWarning)
/usr/local/lib/python3.7/site-packages/urllib3/connectionpool.py:857: InsecureRequestWarning: Unverified HTTPS request is being made. Adding certificate verification is strongly advised. See: https://urllib3.readthedocs.io/en/latest/advanced-usage.html#ssl-warnings
  InsecureRequestWarning)
/usr/local/lib/python3.7/site-packages/urllib3/connectionpool.py:857: InsecureRequestWarning: Unverified HTTPS request is be

/usr/local/lib/python3.7/site-packages/urllib3/connectionpool.py:857: InsecureRequestWarning: Unverified HTTPS request is being made. Adding certificate verification is strongly advised. See: https://urllib3.readthedocs.io/en/latest/advanced-usage.html#ssl-warnings
  InsecureRequestWarning)
/usr/local/lib/python3.7/site-packages/urllib3/connectionpool.py:857: InsecureRequestWarning: Unverified HTTPS request is being made. Adding certificate verification is strongly advised. See: https://urllib3.readthedocs.io/en/latest/advanced-usage.html#ssl-warnings
  InsecureRequestWarning)
/usr/local/lib/python3.7/site-packages/urllib3/connectionpool.py:857: InsecureRequestWarning: Unverified HTTPS request is being made. Adding certificate verification is strongly advised. See: https://urllib3.readthedocs.io/en/latest/advanced-usage.html#ssl-warnings
  InsecureRequestWarning)
/usr/local/lib/python3.7/site-packages/urllib3/connectionpool.py:857: InsecureRequestWarning: Unverified HTTPS request is be

/usr/local/lib/python3.7/site-packages/urllib3/connectionpool.py:857: InsecureRequestWarning: Unverified HTTPS request is being made. Adding certificate verification is strongly advised. See: https://urllib3.readthedocs.io/en/latest/advanced-usage.html#ssl-warnings
  InsecureRequestWarning)
/usr/local/lib/python3.7/site-packages/urllib3/connectionpool.py:857: InsecureRequestWarning: Unverified HTTPS request is being made. Adding certificate verification is strongly advised. See: https://urllib3.readthedocs.io/en/latest/advanced-usage.html#ssl-warnings
  InsecureRequestWarning)
/usr/local/lib/python3.7/site-packages/urllib3/connectionpool.py:857: InsecureRequestWarning: Unverified HTTPS request is being made. Adding certificate verification is strongly advised. See: https://urllib3.readthedocs.io/en/latest/advanced-usage.html#ssl-warnings
  InsecureRequestWarning)
/usr/local/lib/python3.7/site-packages/urllib3/connectionpool.py:857: InsecureRequestWarning: Unverified HTTPS request is be

날짜 국회의원  인용 횟수  \
0    20181010  민경욱  29      
1    20181010  박덕흠  19      
2    20181010  김경진  18      
3    20181010  정진석  17      
4    20181010  김진태  17      
5    20181011  손혜원  20      
6    20181011  김무성  18      
7    20181011  김진태  15      
8    20181011  권미혁  15      
9    20181011  황희   14      
10   20181012  장제원  20      
11   20181012  조응천  16      
12   20181012  이은재  15      
13   20181012  김도읍  10      
14   20181012  박대출  10      
15   20181013  박용진  8       
17   20181013  정우택  2       
18   20181013  위성곤  2       
19   20181013  송영길  2       
20   20181013  변재일  2       
21   20181014  전해철  6       
26   20181014  소병훈  6       
27   20181014  김병욱  5       
28   20181014  박용진  4       
29   20181014  이상민  4       
30   20181015  박용진  27      
31   20181015  엄용수  11      
32   20181015  지상욱  11      
33   20181015  권미혁  11      
34   20181015  박완주  10      
35   20181016  박용진  23      
36   20181016  강병원  19      
37   20181016  추경호  16      
38   20181016  황희   15      
42   20181016  심상정  14      
43   20181017  박용진  20      
44   20181017  김영진  13      
45   20181017  박선숙  7       
47   20181017  전희경  6       
48   20181017  권성동  6       
49   20181018  유민봉  17      
50   20181018  김영우  15      
51   20181018  김현아  13      
52   20181018  김규환  13      
53   20181018  김도읍  13      
54   20181019  이채익  26      
56   20181019  유성엽  16      
58   20181019  김영우  16      
59   20181019  조정식  13      
60   20181019  장제원  11      
61   20181020  박완수  4       
62   20181020  소병훈  3       
63   20181020  박용진  3       
65   20181020  장제원  2       
67   20181020  신용현  2       
69   20181021  박용진  7       
70   20181021  박완주  5       
71   20181021  서청원  4       
72   20181021  김종훈  3       
73   20181021  정우택  3       
74   20181022  김경협  13      
75   20181022  황희   10      
76   20181022  김영우  10      
77   20181022  전현희  10      
78   20181022  민경욱  10      
79   20181023  주승용  15      
80   20181023  남인순  14      
81   20181023  권은희  13      
82   20181023  강창일  11      
83   20181023  김영우  10      
84   20181024  한정애  10      
85   20181024  소병훈  8       
86   20181024  민경욱  7       
87   20181024  박재호  7       
88   20181024  김영진  6       
89   20181025  김병욱  7       
90   20181025  홍철호  7       
91   20181025  한정애  7       
93   20181025  윤관석  7       
94   20181025  강효상  7       
95   20181026  김병욱  10      
97   20181026  이재정  8       
98   20181026  김종석  8       
101  20181026  김성태  7       
102  20181026  이진복  6       
103  20181027  강효상  3       
104  20181027  박용진  3       
105  20181027  홍문표  3       
106  20181027  김병욱  2       
107  20181027  권칠승  2       
108  20181028  하태경  13      
109  20181028  소병훈  4       
111  20181028  홍문표  3       
112  20181028  강길부  2       
113  20181028  김종회  2       
114  20181029  박용진  17      
115  20181029  정진석  9       
116  20181029  신용현  9       
117  20181029  이채익  8       
118  20181029  박주민  8       
119  20181030  박주민  5       
120  20181030  김재경  4       
121  20181030  권성동  3       
122  20181030  천정배  3       
123  20181030  장제원  3       

                                                                                                                                                                                                                                                             인용문  \
0    2013년부터 2017년까지 수도권에서 그린벨트를 해제한 19개 지역 가운데 작년 말 해제된 경기 부천, 서울 강동, 인천 남동구를 제외한 16개 지역에서 주택 매매가격이 평균 5% 상승했다                                                                                                                                                    
1    국민은행의 30년간 서울 아파트 매매가격지수를 보면 민주당이 집권할 때마다 집값이 폭등한다                                                                                                                                                                                                            
2    구글은 세계 각국의 조세법을 어겨가며 수치스러운 장사를 하고 있다                                                                                                                   

In [25]:
df_top5.fillna('', inplace=True); df_top5

날짜 국회의원  인용 횟수  \
0    20181010  민경욱  29      
1    20181010  박덕흠  19      
2    20181010  김경진  18      
3    20181010  정진석  17      
4    20181010  김진태  17      
5    20181011  손혜원  20      
6    20181011  김무성  18      
7    20181011  김진태  15      
8    20181011  권미혁  15      
9    20181011  황희   14      
10   20181012  장제원  20      
11   20181012  조응천  16      
12   20181012  이은재  15      
13   20181012  김도읍  10      
14   20181012  박대출  10      
15   20181013  박용진  8       
17   20181013  정우택  2       
18   20181013  위성곤  2       
19   20181013  송영길  2       
20   20181013  변재일  2       
21   20181014  전해철  6       
26   20181014  소병훈  6       
27   20181014  김병욱  5       
28   20181014  박용진  4       
29   20181014  이상민  4       
30   20181015  박용진  27      
31   20181015  엄용수  11      
32   20181015  지상욱  11      
33   20181015  권미혁  11      
34   20181015  박완주  10      
35   20181016  박용진  23      
36   20181016  강병원  19      
37   20181016  추경호  16      
38   20181016  황희   15      
42   20181016  심상정  14      
43   20181017  박용진  20      
44   20181017  김영진  13      
45   20181017  박선숙  7       
47   20181017  전희경  6       
48   20181017  권성동  6       
49   20181018  유민봉  17      
50   20181018  김영우  15      
51   20181018  김현아  13      
52   20181018  김규환  13      
53   20181018  김도읍  13      
54   20181019  이채익  26      
56   20181019  유성엽  16      
58   20181019  김영우  16      
59   20181019  조정식  13      
60   20181019  장제원  11      
61   20181020  박완수  4       
62   20181020  소병훈  3       
63   20181020  박용진  3       
65   20181020  장제원  2       
67   20181020  신용현  2       
69   20181021  박용진  7       
70   20181021  박완주  5       
71   20181021  서청원  4       
72   20181021  김종훈  3       
73   20181021  정우택  3       
74   20181022  김경협  13      
75   20181022  황희   10      
76   20181022  김영우  10      
77   20181022  전현희  10      
78   20181022  민경욱  10      
79   20181023  주승용  15      
80   20181023  남인순  14      
81   20181023  권은희  13      
82   20181023  강창일  11      
83   20181023  김영우  10      
84   20181024  한정애  10      
85   20181024  소병훈  8       
86   20181024  민경욱  7       
87   20181024  박재호  7       
88   20181024  김영진  6       
89   20181025  김병욱  7       
90   20181025  홍철호  7       
91   20181025  한정애  7       
93   20181025  윤관석  7       
94   20181025  강효상  7       
95   20181026  김병욱  10      
97   20181026  이재정  8       
98   20181026  김종석  8       
101  20181026  김성태  7       
102  20181026  이진복  6       
103  20181027  강효상  3       
104  20181027  박용진  3       
105  20181027  홍문표  3       
106  20181027  김병욱  2       
107  20181027  권칠승  2       
108  20181028  하태경  13      
109  20181028  소병훈  4       
111  20181028  홍문표  3       
112  20181028  강길부  2       
113  20181028  김종회  2       
114  20181029  박용진  17      
115  20181029  정진석  9       
116  20181029  신용현  9       
117  20181029  이채익  8       
118  20181029  박주민  8       
119  20181030  박주민  5       
120  20181030  김재경  4       
121  20181030  권성동  3       
122  20181030  천정배  3       
123  20181030  장제원  3       

                                                                                                                                                                                                                                                             인용문  \
0    2013년부터 2017년까지 수도권에서 그린벨트를 해제한 19개 지역 가운데 작년 말 해제된 경기 부천, 서울 강동, 인천 남동구를 제외한 16개 지역에서 주택 매매가격이 평균 5% 상승했다                                                                                                                                                    
1    국민은행의 30년간 서울 아파트 매매가격지수를 보면 민주당이 집권할 때마다 집값이 폭등한다                                                                                                                                                                                                            
2    구글은 세계 각국의 조세법을 어겨가며 수치스러운 장사를 하고 있다                                                                                                                   

In [26]:
def div_center(s):
    return f'<div style="text-align:center">{s}</div>'

def br_n(n):
    return '<br>'*n

def a_link(s, href):
    return f'<a href={href}>{s}</a>'

def span_underline(s):
    return f'<u>{s}</u>'

def parse_date(date):
    return date[:4] + '\t' + date[4:6] + '\t' + date[6:8].lstrip('0') + '\t\t'

def display_date(date):
    date = date[:4] + '년 ' + date[4:6] + '월 ' + date[6:8].lstrip('0') + '일'
    return div_center(date) + '\t\t'

def quote_count(n):
    return f' ({n}회)'

def quote_source(c):
    return f' ({c})'

In [27]:
'''
2018	10	8		2018	10	8		<div style='text-align:center;'>2018년 10월 8일</div>	
<div style='text-align: center'>이상헌<br>현재 외국인 관광객의 80% 정도는 서울 및 수도권에 몰리는 반면, 타 지방을 방문하는 외국인 관광객은 미미한 수준이라며, 실질적 규제혁신과 제도개선을 통해 지방에 제대로 된 관광인프라가 확충되어야 한다
<br><br>
김병욱<br>청년실업 등으로 신용등급이 낮고 형편이 어려운 20대가 은행권에서 대출을 받지 못하고 금리가 높은 대부업체로 내몰린 뒤 상환능력이 떨어져 연체율이 증가하고 있는 것
<br><br>
강효상<br>지난 6월29일 물산업클러스터 위탁운영기관으로 한국환경공단이 한국수자원공사를 제치고 선정된 배경에는 환경부의 밀어주기 의혹이 있다
<br><br>
강효상<br>지난 6월29일 물산업클러스터 위탁운영기관으로 한국환경공단이 한국수자원공사를 제치고 선정된 배경에는 환경부의 밀어주기 의혹이 있다
<br><br>
강효상<br>지난 6월29일 물산업클러스터 위탁운영기관으로 한국환경공단이 한국수자원공사를 제치고 선정된 배경에는 환경부의 밀어주기 의혹이 있다
<br><br>
강효상<br>지난 6월29일 물산업클러스터 위탁운영기관으로 한국환경공단이 한국수자원공사를 제치고 선정된 배경에는 환경부의 밀어주기 의혹이 있다
<br><br>
<a href='http://newslabit.hankyung.com/article/201806076914G#foo' target='_parent'>10월 8일 전체보기</a></div>

날짜	국회의원	인용 횟수	인용문	언론사	뉴스 식별자	url	url_hankhyung
'''

"\n2018\t10\t8\t\t2018\t10\t8\t\t<div style='text-align:center;'>2018년 10월 8일</div>\t\n<div style='text-align: center'>이상헌<br>현재 외국인 관광객의 80% 정도는 서울 및 수도권에 몰리는 반면, 타 지방을 방문하는 외국인 관광객은 미미한 수준이라며, 실질적 규제혁신과 제도개선을 통해 지방에 제대로 된 관광인프라가 확충되어야 한다\n<br><br>\n김병욱<br>청년실업 등으로 신용등급이 낮고 형편이 어려운 20대가 은행권에서 대출을 받지 못하고 금리가 높은 대부업체로 내몰린 뒤 상환능력이 떨어져 연체율이 증가하고 있는 것\n<br><br>\n강효상<br>지난 6월29일 물산업클러스터 위탁운영기관으로 한국환경공단이 한국수자원공사를 제치고 선정된 배경에는 환경부의 밀어주기 의혹이 있다\n<br><br>\n강효상<br>지난 6월29일 물산업클러스터 위탁운영기관으로 한국환경공단이 한국수자원공사를 제치고 선정된 배경에는 환경부의 밀어주기 의혹이 있다\n<br><br>\n강효상<br>지난 6월29일 물산업클러스터 위탁운영기관으로 한국환경공단이 한국수자원공사를 제치고 선정된 배경에는 환경부의 밀어주기 의혹이 있다\n<br><br>\n강효상<br>지난 6월29일 물산업클러스터 위탁운영기관으로 한국환경공단이 한국수자원공사를 제치고 선정된 배경에는 환경부의 밀어주기 의혹이 있다\n<br><br>\n<a href='http://newslabit.hankyung.com/article/201806076914G#foo' target='_parent'>10월 8일 전체보기</a></div>\n\n날짜\t국회의원\t인용 횟수\t인용문\t언론사\t뉴스 식별자\turl\turl_hankhyung\n"

In [28]:
d = defaultdict(list)
for i, row in df_top5.iterrows():
    date = row['날짜']
    d[date].append(row)
result = ''

for date, row_list in d.items():
    result += parse_date(date)
    result += parse_date(date)
    result += br_n(1) + display_date(date)
    body = ''
    for row in row_list:
        name = row['국회의원']
        said = row['인용문']
        company = row['언론사']
        href = row['url_hankyung']
        cnt = quote_count(row['인용 횟수'])
        source = quote_source(company)
        if company == '한국경제':
            said = span_underline(a_link(said, href))
        body += name + cnt + br_n(1) + said + source + br_n(2)
    result += body
    result += '\n'

result

# data_dir = '/Users/jake/OneDrive - leverage innovative users/Documents/News_Item/Audit_quote/'
# file = 'result.tsv'

# with open(os.path.join(data_dir, file), 'w') as f:
#     f.write(result)

# result.to_csv(os.path.join(data_dir, file), sep='\t', index=False)

'2018\t10\t10\t\t2018\t10\t10\t\t<br><div style="text-align:center">2018년 10월 10일</div>\t\t민경욱 (29회)<br><u><a href=http://news.hankyung.com/article/2018101003711>2013년부터 2017년까지 수도권에서 그린벨트를 해제한 19개 지역 가운데 작년 말 해제된 경기 부천, 서울 강동, 인천 남동구를 제외한 16개 지역에서 주택 매매가격이 평균 5% 상승했다</a></u> (한국경제)<br><br>박덕흠 (19회)<br>국민은행의 30년간 서울 아파트 매매가격지수를 보면 민주당이 집권할 때마다 집값이 폭등한다 (머니투데이)<br><br>김경진 (18회)<br><u><a href=http://news.hankyung.com/article/2018101003481>구글은 세계 각국의 조세법을 어겨가며 수치스러운 장사를 하고 있다</a></u> (한국경제)<br><br>정진석 (17회)<br><u><a href=http://news.hankyung.com/article/2018101003191>강 장관의 발언은 5 24 조치 해제를 기정사실화하는 발언을 한 것 발언 자체에 대해 사과해야 옳다 남북 정상회담 후 폼페이오 장관이 전화 통화에서 남북 군사합의에 강한 불만을 제기했느냐</a></u> (한국경제)<br><br>김진태 (17회)<br>대전동물원에서 탈출했다가 사살된 퓨마와 비슷하게 생긴 동물을 가져왔다 (서울경제)<br><br>\n2018\t10\t11\t\t2018\t10\t11\t\t<br><div style="text-align:center">2018년 10월 11일</div>\t\t손혜원 (20회)<br><u><a href=http://news.hankyung.com/article/2018101119727>선수 선발 과정에 청탁이 있지 않았냐 소신에 따른 현장의 결정이었다 사과하시든지, 사퇴하시든지 하라 선 감독 때문에 프로야구 관객이

# Insert to DB

In [32]:
with MyMongo() as db:
    db.delete_and_insert_df('audit_quote', 'top_5_quote_per_day', df_top5)

<--Mongo Connected.
{}
Deleted rows: 105
Inserted rows: 105
Mongo Connection Closed.-->


# Export tsv

In [30]:
# data_dir = '/Users/jake/OneDrive - leverage innovative users/Documents/News_Item/Audit_quote/'
# file = 'top_5_quote_per_day.tsv'

# df_top5.to_csv(os.path.join(data_dir, file), sep='\t', index=False)

In [31]:
# data_dir = '/Users/jake/OneDrive - leverage innovative users/Documents/News_Item/Audit_quote/'
# file = 'quote_all.tsv'

# quote.loc[::, cols].to_csv(os.path.join(data_dir, file), sep='\t', index=False)